In [63]:
import httpx
import zipfile
from datetime import datetime, timezone, timedelta
import pandas as pd
from io import BytesIO
import time
import pytz
import os

from typing import List

from backtesting import Backtest, Strategy
from backtesting.lib import crossover
import talib as ta

import duckdb

In [ ]:
DOWNLOAD_DATA : bool = False # switch to true to download data
KLINE_INTERVAL = "1m"
BASE_URL_TEMPLATE = "https://data.binance.vision/data/futures/um/daily/klines/{symbol}/{interval}/{symbol}-{interval}-{date_str}.zip"
SYMBOLS = [
    "BTCUSDT"
]
LOCAL_TZ = pytz.timezone("Asia/Singapore")

In [57]:
def download_historical(symbols : List[str], interval : List[str], days_ago=180) :
    columns = [
        "open_time",
        "open",
        "high",
        "low",
        "close",
        "volume",
        "close_time",
        "quote_volume",
        "count",
        "taker_buy_volume",
        "taker_buy_quote_volume",
        "ignore"
    ]

    daterange_end = datetime.now(LOCAL_TZ).astimezone(timezone.utc) - timedelta(minutes=60 * 30) # Data delivered around 3-4am UTC
    daterange_start = daterange_end - timedelta(days=days_ago)
    
    extract_dates = [date.date().strftime("%Y-%m-%d") for date in pd.date_range(start=daterange_start, end=daterange_end)]

    for symbol in symbols :
        symbol_dir = f"./historical/futures_klines_{interval}/{symbol}/"
        os.makedirs(symbol_dir, exist_ok=True)
        for dt in extract_dates :
            url = BASE_URL_TEMPLATE.format(symbol=symbol, date_str=dt, interval=interval)
            target_file = symbol_dir + f"{dt.replace('-','')}.parquet"
            if os.path.exists(target_file) :
                continue
            response = httpx.get(url)
            response.raise_for_status()

            with zipfile.ZipFile(BytesIO(response.content)) as z:
                # There should be only one file inside the zip
                csv_filename = z.namelist()[0]

                with z.open(csv_filename) as f:
                    df = pd.read_csv(f, names=columns, skiprows=1)
                    df = df[df["ignore"] != 1]
                    df.drop("ignore", axis=1, inplace=True)
                    df["open_time"] = pd.to_datetime(df["open_time"], unit="ms")
                    df["close_time"] = pd.to_datetime(df["close_time"], unit="ms")
                    df["date"] = pd.to_datetime(dt)
                    df.to_parquet(target_file, index=False)

            time.sleep(0.2)

In [58]:
if DOWNLOAD_DATA : 
    download_historical(
        symbols=SYMBOLS,
        interval=KLINE_INTERVAL,
    )

In [79]:
symbol = "BTCUSDT"
symbol_dir = f"./historical/futures_klines_1m/{symbol}/*.parquet"


dd_query = f"""
    SELECT 
        close_time AS timestamp, 
        open/1000 AS Open, 
        high/1000 as High, 
        low/1000 as Low, 
        close/1000 AS Close, 
        volume * 1000 AS Volume  
    FROM read_parquet("{symbol_dir}")
"""


df = duckdb.query(dd_query).to_df()
df.set_index("timestamp", inplace=True)

In [88]:
class MACDStrategy(Strategy):
    fastperiod = 12
    slowperiod = 26
    signalperiod = 9

    def init(self):
        # Precompute the two moving averages
        macd_line_raw, signal_line_raw, hist_raw = ta.MACD(
             self.data.Close
        )
        
        self.macd_line = self.I(lambda: macd_line_raw, name='MACD')
        self.signal_line = self.I(lambda: signal_line_raw, name='Signal')
        self.hist = self.I(lambda: hist_raw, name='Histogram')

    def next(self):
            # Check for buy signal: MACD line crosses above Signal line
            if crossover(self.macd_line, self.signal_line):
                # Close any existing short positions and buy
                self.position.close() # Closes any existing position (long or short)
                self.buy()

            # Check for sell signal: MACD line crosses below Signal line
            elif crossover(self.signal_line, self.macd_line):
                # Close any existing long positions and sell
                self.position.close() # Closes any existing position
                self.sell()
                

In [ ]:
bt = Backtest(df, MACDStrategy, cash=10_000, commission=.002)
stats = bt.run()
stats

Backtest.run:   0%|          | 0/260606 [00:00<?, ?bar/s]

/home/yaphoa/.pyenv/versions/3.13.2/lib/python3.13/site-packages/backtesting/backtesting.py:954: UserWarning: time=37496: Broker canceled the relative-sized order due to insufficient margin.
  warnings.warn(
/home/yaphoa/.pyenv/versions/3.13.2/lib/python3.13/site-packages/backtesting/backtesting.py:954: UserWarning: time=37517: Broker canceled the relative-sized order due to insufficient margin.
  warnings.warn(
/home/yaphoa/.pyenv/versions/3.13.2/lib/python3.13/site-packages/backtesting/backtesting.py:954: UserWarning: time=37533: Broker canceled the relative-sized order due to insufficient margin.
  warnings.warn(
/home/yaphoa/.pyenv/versions/3.13.2/lib/python3.13/site-packages/backtesting/backtesting.py:954: UserWarning: time=37556: Broker canceled the relative-sized order due to insufficient margin.
  warnings.warn(
/home/yaphoa/.pyenv/versions/3.13.2/lib/python3.13/site-packages/backtesting/backtesting.py:954: UserWarning: time=37564: Broker canceled the relative-sized order due t

Start                     2024-12-12 00:00...
End                       2025-06-10 23:59...
Duration                    180 days 23:59:00
Exposure Time [%]                    14.70688
Equity Final [$]                     74.34547
Equity Peak [$]                    10000000.0
Commissions [$]                10059813.43703
Return [%]                          -99.99926
Buy & Hold Return [%]                 9.25061
Return (Ann.) [%]                      -100.0
Volatility (Ann.) [%]                     0.0
CAGR [%]                               -100.0
Sharpe Ratio                 -351464627.68608
Sortino Ratio                        -0.39318
Calmar Ratio                         -1.00001
Alpha [%]                           -99.97249
Beta                                 -0.00289
Max. Drawdown [%]                   -99.99926
Avg. Drawdown [%]                   -99.99926
Max. Drawdown Duration      180 days 23:25:00
Avg. Drawdown Duration      180 days 23:25:00
# Trades                          